In [32]:
import torch

In [33]:
use_cuda = torch.cuda.is_available()

In [34]:
use_cuda

True

## Importing Libraries


In [35]:
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs
import sklearn
from sklearn.metrics import classification_report
from sklearn.metrics import f1_score

## Loading Files From Dataset

In [37]:
df = pd.read_csv("Emotion_Analysis_Task_B_train.tsv",sep='\t')
df_eval = pd.read_csv("Emotion_Analysis_Task_B_dev.tsv",sep='\t')
df_test = pd.read_csv("Emotion_Analysis_Task_B_test.csv",sep='\t')

In [38]:
df_eval.rename(columns={'category':'Labels','text':'Text'},inplace=True)
df_eval = df_eval[['Text','Labels']]
df.rename(columns={'category':'Labels','text':'Text'},inplace=True)
df = df[['Text','Labels']]
df_test.rename(columns={'category':'Labels','text':'Text'},inplace=True)
df_test = df_test[['Text','Labels']]

In [39]:
num_labels = len(df['Labels'].unique())
keys = list(df['Labels'].unique())
values = list(range(0, num_labels))
label_dict = dict(zip(keys,values))
df['Labels'] = df['Labels'].apply(lambda x:label_dict[x])
df_eval['Labels'] = df_eval['Labels'].apply(lambda x:label_dict[x])
df_test['Labels'] = df_test['Labels'].apply(lambda x:label_dict[x])
num_labels

31

## Balancing the imbalanced dataset

In [40]:
def oversample(df):
        classes = df['Labels'].value_counts().to_dict()
        most = max(classes.values())
        classes_list = []
        for key in classes:
            classes_list.append(df[df['Labels'] == key]) 
        classes_sample = []
        for i in range(1,len(classes_list)):
            classes_sample.append(classes_list[i].sample(most, replace=True))
        df_maybe = pd.concat(classes_sample)
        final_df = pd.concat([df_maybe,classes_list[0]], axis=0)
        final_df = final_df.reset_index(drop=True)
        return pd.DataFrame({'Text': final_df['Text'].tolist(), 'Labels': final_df['Labels'].tolist()})

In [41]:
def over_under_sample(df):
  unq_labels = list(set(df['Labels'].tolist()))
  texts = df['Text'].tolist()
  labels = df['Labels'].tolist()
  data_dict = dict()

  for l in unq_labels:
    data_dict[l] = []

  for i in range(len(texts)):
    data_dict[labels[i]].append(texts[i])

  req_len = len(labels)//len(unq_labels)

  for label in data_dict:
    if len(data_dict[label]) > req_len:
      data_dict[label] = data_dict[label][:req_len]

    new_texts = []

    new_labels = []      
    for l in data_dict:
      new_texts += data_dict[l]
      new_labels += [l]*len(data_dict[l])
    return oversample(pd.DataFrame({'Text': new_texts, 'Labels': new_labels}))

In [42]:
df = over_under_sample(df)

## Model Training

In [43]:
model_args = ClassificationArgs()

In [44]:
model_args.overwrite_output_dir=True
model_args.eval_batch_size=8
model_args.train_batch_size=8
model_args.learning_rate=4e-5

In [45]:
model = ClassificationModel(
    'bert',
    'google/muril-base-cased',
    num_labels=31,
    args=model_args,
    tokenizer_type="bert",
    tokenizer_name='google/muril-base-cased'
) 

Downloading: 100%|██████████████████████████████| 411/411 [00:00<00:00, 131kB/s]
Downloading: 100%|███████████████████████████| 909M/909M [09:07<00:00, 1.74MB/s]
Some weights of the model checkpoint at google/muril-base-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.dense.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly id

In [46]:
for i in range(0,5):
    !rm -rf /kaggle/working/outputs
    model.train_model(df,eval_data=df_eval,acc=sklearn.metrics.classification_report)
    result, model_outputs, preds_list = model.eval_model(df_test,acc=sklearn.metrics.classification_report)
    for j in result.values():
        print(j)

/usr/local/lib/python3.8/dist-packages/simpletransformers/classification/classification_model.py:585: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(
  0%|                                   | 296/147560 [01:14<10:16:55,  3.98it/s]
/usr/local/lib/python3.8/dist-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
Epochs 0/1. Running Loss:    3.4307:   0%| | 92/18445 [00:25<1:31:21,  3.35it/s]


Epochs 0/1. Running Loss:    3.4307:   1%| | 99/18445 [00:27<1:37:01,  3.15it/s]
Epochs 0/1. Running Loss:    3.4307:   1%| | 100/18445 [00:27<1:37:29,  3.14it/s
Epochs 0/1. Running Loss:    3.4353:   1%| | 100/18445 [00:28<1:37:29,  3.14it/s
Epochs 0/1. Running Loss:    3.4353:   1%| | 101/18445 [00:28<1:37:06,  3.15it/s
Epochs 0/1. Running Loss:    3.4336:   1%| | 101/18445 [00:28<1:37:06,  3.15it/s
Epochs 0/1. Running Loss:    3.4336:   1%| | 102/18445 [00:28<1:38:15,  3.11it/s
Epochs 0/1. Running Loss:    3.4343:   1%| | 102/18445 [00:28<1:38:15,  3.11it/s
Epochs 0/1. Running Loss:    3.4343:   1%| | 103/18445 [00:29<1:45:34,  2.90it/s
Epochs 0/1. Running Loss:    3.4368:   1%| | 103/18445 [00:29<1:45:34,  2.90it/s
Epochs 0/1. Running Loss:    3.4368:   1%| | 104/18445 [00:29<1:49:01,  2.80it/s
Epochs 0/1. Running Loss:    3.4355:   1%| | 104/18445 [00:29<1:49:01,  2.80it/s
Epochs 0/1. Running Loss:    3.4355:   1%| | 105/18445 [00:29<1:47:10,  2.85it/s
Epochs 0/1. Running Loss:   

Epochs 0/1. Running Loss:    3.4368:   1%| | 190/18445 [01:00<1:49:43,  2.77it/s
Epochs 0/1. Running Loss:    3.4338:   1%| | 190/18445 [01:01<1:49:43,  2.77it/s
Epochs 0/1. Running Loss:    3.4338:   1%| | 191/18445 [01:01<1:52:27,  2.71it/s
Epochs 0/1. Running Loss:    3.4331:   1%| | 191/18445 [01:01<1:52:27,  2.71it/s
Epochs 0/1. Running Loss:    3.4331:   1%| | 192/18445 [01:01<1:49:51,  2.77it/s
Epochs 0/1. Running Loss:    3.4336:   1%| | 192/18445 [01:01<1:49:51,  2.77it/s
Epochs 0/1. Running Loss:    3.4336:   1%| | 193/18445 [01:02<1:51:24,  2.73it/s
Epochs 0/1. Running Loss:    3.4346:   1%| | 193/18445 [01:02<1:51:24,  2.73it/s
Epochs 0/1. Running Loss:    3.4346:   1%| | 194/18445 [01:02<1:59:17,  2.55it/s
Epochs 0/1. Running Loss:    3.4309:   1%| | 194/18445 [01:02<1:59:17,  2.55it/s
Epochs 0/1. Running Loss:    3.4309:   1%| | 195/18445 [01:02<2:02:10,  2.49it/s
Epochs 0/1. Running Loss:    3.4329:   1%| | 195/18445 [01:03<2:02:10,  2.49it/s
Epochs 0/1. Running Loss:   

Epochs 0/1. Running Loss:    3.4336:   2%| | 287/18445 [01:31<1:19:36,  3.80it/s
Epochs 0/1. Running Loss:    3.4365:   2%| | 287/18445 [01:31<1:19:36,  3.80it/s
Epochs 0/1. Running Loss:    3.4365:   2%| | 288/18445 [01:31<1:19:09,  3.82it/s
Epochs 0/1. Running Loss:    3.4331:   2%| | 288/18445 [01:31<1:19:09,  3.82it/s
Epochs 0/1. Running Loss:    3.4331:   2%| | 289/18445 [01:31<1:18:55,  3.83it/s
Epochs 0/1. Running Loss:    3.4319:   2%| | 289/18445 [01:31<1:18:55,  3.83it/s
Epochs 0/1. Running Loss:    3.4319:   2%| | 290/18445 [01:31<1:18:39,  3.85it/s
Epochs 0/1. Running Loss:    3.4355:   2%| | 290/18445 [01:32<1:18:39,  3.85it/s
Epochs 0/1. Running Loss:    3.4355:   2%| | 291/18445 [01:32<1:18:32,  3.85it/s
Epochs 0/1. Running Loss:    3.4285:   2%| | 291/18445 [01:32<1:18:32,  3.85it/s
Epochs 0/1. Running Loss:    3.4285:   2%| | 292/18445 [01:32<1:18:26,  3.86it/s
Epochs 0/1. Running Loss:    3.4331:   2%| | 292/18445 [01:32<1:18:26,  3.86it/s
Epochs 0/1. Running Loss:   

Epochs 0/1. Running Loss:    3.4270:   2%| | 384/18445 [02:00<1:46:13,  2.83it/s
Epochs 0/1. Running Loss:    3.4331:   2%| | 384/18445 [02:00<1:46:13,  2.83it/s
Epochs 0/1. Running Loss:    3.4331:   2%| | 385/18445 [02:00<1:46:38,  2.82it/s
Epochs 0/1. Running Loss:    3.4329:   2%| | 385/18445 [02:00<1:46:38,  2.82it/s
Epochs 0/1. Running Loss:    3.4329:   2%| | 386/18445 [02:01<1:47:09,  2.81it/s
Epochs 0/1. Running Loss:    3.4326:   2%| | 386/18445 [02:01<1:47:09,  2.81it/s
Epochs 0/1. Running Loss:    3.4326:   2%| | 387/18445 [02:01<1:46:48,  2.82it/s
Epochs 0/1. Running Loss:    3.4351:   2%| | 387/18445 [02:01<1:46:48,  2.82it/s
Epochs 0/1. Running Loss:    3.4351:   2%| | 388/18445 [02:01<1:47:20,  2.80it/s
Epochs 0/1. Running Loss:    3.4382:   2%| | 388/18445 [02:02<1:47:20,  2.80it/s
Epochs 0/1. Running Loss:    3.4382:   2%| | 389/18445 [02:02<1:46:42,  2.82it/s
Epochs 0/1. Running Loss:    3.4314:   2%| | 389/18445 [02:02<1:46:42,  2.82it/s
Epochs 0/1. Running Loss:   

...

Epochs 0/1. Running Loss:    0.8053:  40%|▍| 7368/18445 [1:00:41<52:59,  3.48it/
Epochs 0/1. Running Loss:    1.2082:  40%|▍| 7368/18445 [1:00:41<52:59,  3.48it/
Epochs 0/1. Running Loss:    1.2082:  40%|▍| 7369/18445 [1:00:41<52:53,  3.49it/
Epochs 0/1. Running Loss:    1.2532:  40%|▍| 7369/18445 [1:00:41<52:53,  3.49it/
Epochs 0/1. Running Loss:    1.2532:  40%|▍| 7370/18445 [1:00:41<52:55,  3.49it/
Epochs 0/1. Running Loss:    0.4467:  40%|▍| 7370/18445 [1:00:41<52:55,  3.49it/
Epochs 0/1. Running Loss:    0.4467:  40%|▍| 7371/18445 [1:00:41<52:59,  3.48it/
Epochs 0/1. Running Loss:    1.0324:  40%|▍| 7371/18445 [1:00:41<52:59,  3.48it/
Epochs 0/1. Running Loss:    1.0324:  40%|▍| 7372/18445 [1:00:42<52:52,  3.49it/
Epochs 0/1. Running Loss:    1.1854:  40%|▍| 7372/18445 [1:00:42<52:52,  3.49it/
Epochs 0/1. Running Loss:    1.1854:  40%|▍| 7373/18445 [1:00:42<52:45,  3.50it/
Epochs 0/1. Running Loss:    0.9041:  40%|▍| 7373/18445 [1:00:42<52:45,  3.50it/
Epochs 0/1. Running Loss:   

Epochs 0/1. Running Loss:    2.3041:  40%|▍| 7465/18445 [1:01:20<1:34:22,  1.94i
Epochs 0/1. Running Loss:    1.9617:  40%|▍| 7465/18445 [1:01:20<1:34:22,  1.94i
Epochs 0/1. Running Loss:    1.9617:  40%|▍| 7466/18445 [1:01:20<1:34:56,  1.93i
Epochs 0/1. Running Loss:    0.7237:  40%|▍| 7466/18445 [1:01:21<1:34:56,  1.93i
Epochs 0/1. Running Loss:    0.7237:  40%|▍| 7467/18445 [1:01:21<1:35:28,  1.92i
Epochs 0/1. Running Loss:    1.3938:  40%|▍| 7467/18445 [1:01:21<1:35:28,  1.92i
Epochs 0/1. Running Loss:    1.3938:  40%|▍| 7468/18445 [1:01:21<1:34:08,  1.94i
Epochs 0/1. Running Loss:    1.2209:  40%|▍| 7468/18445 [1:01:22<1:34:08,  1.94i
Epochs 0/1. Running Loss:    1.2209:  40%|▍| 7469/18445 [1:01:22<1:36:30,  1.90i
Epochs 0/1. Running Loss:    0.5898:  40%|▍| 7469/18445 [1:01:22<1:36:30,  1.90i
Epochs 0/1. Running Loss:    0.5898:  40%|▍| 7470/18445 [1:01:22<1:37:36,  1.87i
Epochs 0/1. Running Loss:    1.4952:  40%|▍| 7470/18445 [1:01:23<1:37:36,  1.87i
Epochs 0/1. Running Loss:   

Epochs 0/1. Running Loss:    0.5739:  41%|▍| 7562/18445 [1:02:09<1:31:20,  1.99i
Epochs 0/1. Running Loss:    1.0376:  41%|▍| 7562/18445 [1:02:09<1:31:20,  1.99i
Epochs 0/1. Running Loss:    1.0376:  41%|▍| 7563/18445 [1:02:09<1:30:34,  2.00i
Epochs 0/1. Running Loss:    0.6387:  41%|▍| 7563/18445 [1:02:09<1:30:34,  2.00i
Epochs 0/1. Running Loss:    0.6387:  41%|▍| 7564/18445 [1:02:10<1:29:53,  2.02i
Epochs 0/1. Running Loss:    1.6347:  41%|▍| 7564/18445 [1:02:10<1:29:53,  2.02i
Epochs 0/1. Running Loss:    1.6347:  41%|▍| 7565/18445 [1:02:10<1:31:09,  1.99i
Epochs 0/1. Running Loss:    0.7875:  41%|▍| 7565/18445 [1:02:10<1:31:09,  1.99i
Epochs 0/1. Running Loss:    0.7875:  41%|▍| 7566/18445 [1:02:11<1:30:26,  2.00i
Epochs 0/1. Running Loss:    1.2665:  41%|▍| 7566/18445 [1:02:11<1:30:26,  2.00i
Epochs 0/1. Running Loss:    1.2665:  41%|▍| 7567/18445 [1:02:11<1:29:34,  2.02i
Epochs 0/1. Running Loss:    0.9774:  41%|▍| 7567/18445 [1:02:11<1:29:34,  2.02i
Epochs 0/1. Running Loss:   

Epochs 0/1. Running Loss:    0.8745:  42%|▍| 7659/18445 [1:02:57<1:34:26,  1.90i
Epochs 0/1. Running Loss:    1.2794:  42%|▍| 7659/18445 [1:02:58<1:34:26,  1.90i
Epochs 0/1. Running Loss:    1.2794:  42%|▍| 7660/18445 [1:02:58<1:34:09,  1.91i
Epochs 0/1. Running Loss:    0.9696:  42%|▍| 7660/18445 [1:02:58<1:34:09,  1.91i
Epochs 0/1. Running Loss:    0.9696:  42%|▍| 7661/18445 [1:02:58<1:32:50,  1.94i
Epochs 0/1. Running Loss:    0.6462:  42%|▍| 7661/18445 [1:02:59<1:32:50,  1.94i
Epochs 0/1. Running Loss:    0.6462:  42%|▍| 7662/18445 [1:02:59<1:33:10,  1.93i
Epochs 0/1. Running Loss:    1.2043:  42%|▍| 7662/18445 [1:02:59<1:33:10,  1.93i
Epochs 0/1. Running Loss:    1.2043:  42%|▍| 7663/18445 [1:02:59<1:32:55,  1.93i
Epochs 0/1. Running Loss:    0.5649:  42%|▍| 7663/18445 [1:03:00<1:32:55,  1.93i
Epochs 0/1. Running Loss:    0.5649:  42%|▍| 7664/18445 [1:03:00<1:33:29,  1.92i
Epochs 0/1. Running Loss:    0.5142:  42%|▍| 7664/18445 [1:03:00<1:33:29,  1.92i
Epochs 0/1. Running Loss:   

KeyboardInterrupt: 

In [ ]:
predictions, raw_outputs = model.predict(df_test['Text'].to_list())

In [ ]:
df_final = df_test.copy()
reverse_label_dict = {v:u for u,v in label_dict.items()}
reverse_label_dict
df_final['Predicted_Labels'] = predictions
df_final['Predicted_Labels'] = df_final['Predicted_Labels'].apply(lambda x:reverse_label_dict[x])
df_final['Labels'] = df_final['Labels'].apply(lambda x:reverse_label_dict[x])
df_final['pid'] = df_final.index
df_final = df_final[['pid','Predicted_Labels','Labels']]

In [ ]:
df_final

In [ ]:
score = f1_score(df_final['Labels'],df_final['Predicted_Labels'],average='macro')
print("The macro average f1 score is:" + str(score))